# Time Series Forecasting - II

Till now we made prediction model for demand capacity planning. For much better planning and management we want to predict the number of late coming <code style="background:yellow;color:black">flights independently based on airports.</code>

> This will enable us to check and manage the `operations` in much better and granular way


The _objectives_ in the following `Notebook` are:

1. Perform Deep Learning Modelling using <code style="background:yellow;color:black">RNN & LSTM based architecture</code> by proper analysis and description. 
2. Generating features with the help of feature engineering as in the case of DL the loss is very different.
3. Perform Comparision by models and trying to find the best one with the help of our metric function.

In [41]:
# run the libraries
import pandas as pd
import numpy as np
import warnings
from sklearn import metrics
from termcolor import colored
import tensorflow as tf
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from tensorflow.keras import Sequential,Model
from tensorflow.keras.layers import Dense, Dropout, LSTM, Activation, TimeDistributed, Flatten,Input,SimpleRNN
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping,TensorBoard
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler, power_transform
warnings.filterwarnings("ignore")
%matplotlib inline
%run viz.py
%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [42]:
# read the data and see it....
df = pd.read_pickle('Aircraft_Data_Analysis.pkl')
df.head()

year  month carrier carrier_name airport  \
0  2019      1      MQ    Envoy Air     SAV   
1  2019      1      MQ    Envoy Air     SDF   
2  2019      1      MQ    Envoy Air     SGF   
3  2019      1      MQ    Envoy Air     SHV   
4  2019      1      MQ    Envoy Air     SJT   

                                        airport_name  arr_flights  \
0   Savannah, GA: Savannah/Hilton Head International         65.0   
1  Louisville, KY: Louisville Muhammad Ali Intern...         61.0   
2      Springfield, MO: Springfield-Branson National        428.0   
3                Shreveport, LA: Shreveport Regional        174.0   
4   San Angelo, TX: San Angelo Regional/Mathis Field        135.0   

   arriving_delay  carrier_ct  weather_ct  ...  arr_diverted  aircraft_delay  \
0           15.01        3.41        0.71  ...           1.0           601.0   
1           18.01        2.70        1.01  ...           0.0           890.0   
2           80.00       13.31        5.18  ...           0.0          3954.0   
3           28.01        5.97        1.17  ...           0.0          1655.0   
4           23.00       10.78        0.35  ...           0.0           835.0   

   carrier_delay  weather_delay  nas_delay  security_delay  \
0          180.0           29.0      129.0             0.0   
1          180.0           36.0      383.0             0.0   
2          705.0          213.0      982.0             0.0   
3          360.0           55.0      268.0             0.0   
4          320.0           27.0      192.0             0.0   

   late_aircraft_delay   latitude   longitude  admin_delay  
0                263.0  32.140799  -81.204129        129.0  
1                291.0  38.254238  -85.759407        383.0  
2               2054.0  37.216678  -93.292037        982.0  
3                972.0  32.522183  -93.765194        268.0  
4                296.0  31.464836 -100.439844        192.0  

[5 rows x 24 columns]

In [43]:
## set the date and drop it
df['date'] = pd.to_datetime(df[['year', 'month']].assign(DAY=1))
df.set_index('date', inplace = True)

## Data Preparation
In this we will perfrom 3 main steps:

1. Select relevant features.
2. Normalise the continous variable and `transform` the categorical variable .
3. Perform standard scaling and prepare the data for modelling.

In [44]:
# let us prepare the dataset
## select the features
df = df[['latitude','longitude','aircraft_delay','month']].sort_index()

df.groupby(['airport_name'])[['latitude','longitude']].mean()

### Cyclic Encoding 

> Since, the time varibales are cyclic in nature we will transform it into __sin and cosine__ components.

This components will make sure the distance between my lowest and largest values are continous

In [45]:
## encode the sin and cos transformations i.e put it into sin and cosine
def encode(df, col, max_val):
    '''
    This function gives sine and cosine transformation of variables by input of cols and max values
    '''
    df[col + '_Sin'] = np.sin(2 * np.pi * df[col]/max_val)
    df[col + '_Cos'] = np.cos(2 * np.pi * df[col]/max_val)
    del df[col]
    return df

In [46]:
## encode the Month
df = encode(df, 'month', 12)

In [47]:
# let us see the data now
d = description(df)
d.data_description(summary = True)

The number of points in this data is 87285 

The shape of the data is (87285, 5) 

Let's see the data : 

The summary of data set is : 
           latitude     longitude  aircraft_delay     month_Sin     month_Cos
count  87285.000000  87285.000000    87285.000000  8.728500e+04  8.728500e+04
mean      37.355778    -91.269096     3847.670848  3.054891e-02  1.425270e-02
std        8.860178     24.445229    11760.328634  7.134764e-01  6.998761e-01
min      -25.420676   -176.573492        0.000000 -1.000000e+00 -1.000000e+00
25%       33.448437   -101.879336      264.000000 -5.000000e-01 -5.000000e-01
50%       38.581061    -87.922497      883.000000  1.224647e-16  6.123234e-17
75%       42.331551    -80.053294     2553.000000  8.660254e-01  8.660254e-01
max       71.387113    144.802060   429194.000000  1.000000e+00  1.000000e+00

The count of n.a values in each column is: 
latitude          0
longitude         0
aircraft_delay    0
month_Sin         0
month_Cos         0
dtype: int64


In [49]:
## lets visualise Month
visualisation(df).line_plot(x = 'month_Sin', y='month_Cos')

> We see the transformation leads to `cyclic values`

In [50]:
## get the variable and target variable
X = df.drop(columns = ['aircraft_delay']).values
y = df['aircraft_delay'].values

```python
# normalising the data with min max scaler
scaler = MinMaxScaler(feature_range=(0, 1))
X      = scaler.fit_transform(X)
y      = scaler.fit_transform(y.reshape(-1, 1))
```

In [51]:
## perform box-cox transformation
X = power_transform(X, method='yeo-johnson',standardize=True)
y = power_transform(y.reshape(-1,1), method='yeo-johnson',standardize=True)

__Just Try Out Idea : Not Implemented__

Since our objective is to minimise loss based on `MAPE` we will transform our __target__ variable to logarithmic value. If we use minimize MSE of __log(y)__ our loss function is:


$$ L=\sum_{i=1}^{n} (log(y_{pred}) - log(y_{true}))^2$$

This will transform to,

$$ L=\sum_{i=1}^{n} (log\frac{y_{pred}}{y_{true}})^2$$

> This is equivalent to minimising our __MAPE__ value for better accuracy.




### Data Tranform

<div class="alert alert-block alert-info">
<b>Code:</b> Since the models which we are using use sequence to sequence encoding we need to take care of shape of our data. The transformation of data is important in this case. For this purpose we will use the custom window to transform the data from 2D to 3D.</div>


In [52]:
def lstm_data_transform(x_data, y_data, num_steps=1):
    """ 
    Changes data to the format for LSTM training for sliding window approach 
    
    This function reshape for lstm into 3 dimension shape (batchsize, timestep, features)

    Input to this function is X and y and time step
    """
    # Prepare the list for the transformed data
    X, y = list(), list()
    # Loop of the entire data set
    for i in range(x_data.shape[0]):
        # compute a new (sliding window) index
        end_ix = i + num_steps
        # if index is larger than the size of the dataset, we stop
        if end_ix >= x_data.shape[0]:
            break
        # Get a sequence of data for x
        seq_X = x_data[i:end_ix]
        # Get only the last element of the sequency for y
        seq_y = y_data[end_ix]
        # Append the list with sequencies
        X.append(seq_X)
        y.append(seq_y)
    # Make final arrays
    x_array = np.array(X)
    y_array = np.array(y)
    return x_array, y_array

### Metrics

In [53]:
def metric_calc(forecast, actual, model_name=None):
        '''
        This calculates the accuracy metrics gives our predicted and test data
        '''
        # Calculate metrics and append it
        mae  = metrics.mean_absolute_error(forecast, actual)
        mape = metrics.mean_absolute_percentage_error(forecast, actual)
        mse  = metrics.mean_squared_error(forecast, actual)
        rmse = np.sqrt(metrics.mean_squared_error(forecast, actual))
        r2   = metrics.r2_score(forecast, actual)
        
        if model_name:
            print(colored("The results of your {} are :".format(model_name),color = 'yellow', attrs=['bold']))
        # print the metrics
        print('Mean Absolute Error:', mae)
        print('Mean Absolute Percentage Error:', mape)
        print('Mean Squared Error:',  mse)
        print('Root Mean Squared Error:', rmse)
        print('R Squared:', r2)        

## Modelling

Two Types of Deep Learning model used here to train the sequential data are:

1. `RNN Model:` The reason to choose this model was to check what is the effect of sequence transformation with the introduction of the <code style="background:yellow;color:black">previous cell state.</code> Our hypothesis is it captures the temporal relationship of our data well.


2. `LSTM Model`: This adds to the RNN model with an extra `Forget Gate` which yields better accuracy.

> This model works well when we have more training data. But in our case, we have less data so let's see how well it performs.


### Random Forest

In [54]:
## train and test split
#y = np.log1p(y)
X_train, X_test, y_train, y_test =  train_test_split(X, y, test_size=0.2,random_state=True)

In [55]:
%%time
## instantiate the model
rf_model = RandomForestRegressor()

# Specifying hyperparams for the search
param_grid = {
            'criterion': ['mae'],
            'n_estimators': [25],
            'max_depth':    [15],
            'min_samples_split': [15],
            'min_samples_leaf' : [25],
            'bootstrap': [True]
            }
# Fit the model and find best hyperparams
grid_model = GridSearchCV(estimator=rf_model, param_grid=param_grid, cv=5, n_jobs=-1)
grid_model.fit(X_train,y_train)

# Fit the model with best params
print()
print("Best parameters =", grid_model.best_params_)
model_clf = rf_model.set_params(**grid_model.best_params_)
model_clf.fit(X_train, y_train)


Best parameters = {'bootstrap': True, 'criterion': 'mae', 'max_depth': 15, 'min_samples_leaf': 25, 'min_samples_split': 15, 'n_estimators': 25}
Wall time: 32min 42s


RandomForestRegressor(criterion='mae', max_depth=15, min_samples_leaf=25,
                      min_samples_split=15, n_estimators=25)

In [75]:
## let us see the accuracy
metric_calc(model_clf.predict(X_test), y_test)

### RNN Model

In [63]:
## transform for LSTM
X, y = lstm_data_transform(X, y, num_steps=3)

In [64]:
## split it into train and test
X_train, X_test, y_train, y_test =  train_test_split(X, y, test_size=0.2,random_state=True)

In [65]:
## define our params
layers = [50]
dense_layer = [150]
dropout = 0.3

In [66]:
## declare the shape
inp = Input(shape=X_train.shape[1:])

## RNN layer
x = SimpleRNN(layers[0], return_sequences=True)(inp)  # add first layer
x = Dropout(dropout)(x)

## Repeat based on values in list with dropout
for i in layers[1:] : 
    x = SimpleRNN(i, activation='relu', return_sequences=True)(x) # add succesiive layers
    x = Dropout(dropout)(x)  # add dropout for layer

## Activate the neuron
x = Activation("relu")(x)

## flatten and add dense layer
x = Flatten()(x)
for i in dense_layer:
    x = Dense(i,activation='relu')(x)  

# add output layer
y = Dense(1,activation='linear')(x)  # output layer with linear activation

## taking log of predicted value
#y = tf.math.log1p(y)

## Instantiate the model
rnn_model = Model(inp,y)

## Set ADAM opt and see the model
opt = Adam(lr = 0.001)
rnn_model.compile(loss="mse", optimizer=opt, metrics=['mae','mse'])
rnn_model.summary()

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 3, 4)]            0         
_________________________________________________________________
simple_rnn_1 (SimpleRNN)     (None, 3, 50)             2750      
_________________________________________________________________
dropout_1 (Dropout)          (None, 3, 50)             0         
_________________________________________________________________
activation_1 (Activation)    (None, 3, 50)             0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 150)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 150)               22650     
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 151 

In [67]:
# Create a checkpoint for models
checkpoint = tf.keras.callbacks.ModelCheckpoint("RNN.h5",monitor="val_mse",verbose = 1,        # creating a callback for saving the model
                                                save_best_only = False,save_weights_only = False, # save the weights
                                                mode= "auto",save_freq= "epoch",                  
                                                options=None)

# tensorboard logs
# Define Tensorboard as a Keras callback
tensorboard = TensorBoard(
  log_dir='.\RNN_logs', histogram_freq=0,write_graph=True, 
  write_grads=False, write_images=False, embeddings_freq=0, embeddings_layer_names=None, 
  embeddings_metadata=None, embeddings_data=None, update_freq='epoch')
keras_callbacks = [tensorboard]


## fit and train
rnn_model.fit(X_train,y_train, epochs=3, batch_size=64,validation_data= (X_test,y_test),
              callbacks = [checkpoint,keras_callbacks])

Epoch 1/3
1092/1092 [==============================] - 20s 16ms/step - loss: 1.0165 - mae: 0.7550 - mse: 1.0165 - val_loss: 0.9948 - val_mae: 0.7474 - val_mse: 0.9948

Epoch 00001: saving model to RNN.h5
Epoch 2/3
1092/1092 [==============================] - 13s 12ms/step - loss: 0.9834 - mae: 0.7432 - mse: 0.9834 - val_loss: 0.9932 - val_mae: 0.7462 - val_mse: 0.9932

Epoch 00002: saving model to RNN.h5
Epoch 3/3
1092/1092 [==============================] - 13s 12ms/step - loss: 0.9857 - mae: 0.7448 - mse: 0.9857 - val_loss: 0.9905 - val_mae: 0.7444 - val_mse: 0.9905

Epoch 00003: saving model to RNN.h5


In [77]:
## let us see the accuracy
metric_calc(rnn_model.predict(X_test),y_test, model_name='RNN')

The results of your RNN are :
Mean Absolute Error: 0.7443619582516163
Mean Absolute Percentage Error: 46.49577240235472
Mean Squared Error: 0.9905288322346947
Root Mean Squared Error: 0.9952531498240509
R Squared: -69.0469472734473


In [ ]:
%tensorboard --logdir=RNN_logs

## LSTM

In [69]:
## define our params
layers = [175]
dense_layer = [25]
dropout = 0.3

In [71]:
## declare the shape
inp = Input(shape=X.shape[1:])

## LSTM layer
x = LSTM(layers[0], return_sequences=True)(inp)  # add first layer

## Repeat based on values in list with dropout
for i in layers[1:] : 
    x = LSTM(i, activation='relu', return_sequences=True)(x) # add succesiive layers
    x = Dropout(dropout)(x)  # add dropout for first layer
    
## adding time distributed layer
x = TimeDistributed(Dense(5))(x)  # add dense layer
x = Activation("relu")(x)

## flatten and add dense layer
x = Flatten()(x)
for i in dense_layer:
    x = Dense(i,activation='relu')(x)  # add output layer

## add output layer
y = Dense(1,activation='linear')(x)  # output layer with linear activation

## taking log of predicted value
#y = tf.math.log1p(y)

## Instantiate the model
lstm_model = Model(inp,y)

## Set ADAM opt and see the model
opt = Adam(lr = 0.001)
lstm_model.compile(loss="mse", optimizer=opt, metrics=['mse'])
lstm_model.summary()

Model: "model_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_4 (InputLayer)         [(None, 3, 4)]            0         
_________________________________________________________________
lstm_1 (LSTM)                (None, 3, 175)            126000    
_________________________________________________________________
time_distributed_1 (TimeDist (None, 3, 5)              880       
_________________________________________________________________
activation_3 (Activation)    (None, 3, 5)              0         
_________________________________________________________________
flatten_3 (Flatten)          (None, 15)                0         
_________________________________________________________________
dense_8 (Dense)              (None, 25)                400       
_________________________________________________________________
dense_9 (Dense)              (None, 1)                 26  

In [72]:
# Create a checkpoint for models
checkpoint = tf.keras.callbacks.ModelCheckpoint("LSTM.h5",monitor="val_mse",verbose = 1,        # creating a callback for saving the model
                                                save_best_only = False,save_weights_only = False, # save the weights
                                                mode= "auto",save_freq= "epoch",                  
                                                options=None)

# tensorboard logs
# Define Tensorboard as a Keras callback
tensorboard = TensorBoard(
  log_dir='.\LSTM_logs', histogram_freq=0,write_graph=True, 
  write_grads=False, write_images=False, embeddings_freq=0, embeddings_layer_names=None, 
  embeddings_metadata=None, embeddings_data=None, update_freq='epoch')
keras_callbacks = [tensorboard]


lstm_model.fit(X_train,y_train, epochs=3, batch_size=512,validation_data= (X_test,y_test),callbacks = [checkpoint,keras_callbacks])

Epoch 1/3
137/137 [==============================] - 16s 72ms/step - loss: 0.9807 - mse: 0.9807 - val_loss: 0.9957 - val_mse: 0.9957

Epoch 00001: saving model to LSTM.h5
Epoch 2/3
137/137 [==============================] - 2s 17ms/step - loss: 0.9786 - mse: 0.9786 - val_loss: 0.9926 - val_mse: 0.9926

Epoch 00002: saving model to LSTM.h5
Epoch 3/3
137/137 [==============================] - 2s 16ms/step - loss: 0.9804 - mse: 0.9804 - val_loss: 0.9927 - val_mse: 0.9927

Epoch 00003: saving model to LSTM.h5


In [73]:
metric_calc(lstm_model.predict(X_test), y_test, model_name='LSTM')

The results of your LSTM are :
Mean Absolute Error: 0.7462075614781961
Mean Absolute Percentage Error: 58.26287936832396
Mean Squared Error: 0.9927279116865306
Root Mean Squared Error: 0.9963573212891701
R Squared: -59.957204761390514


In [ ]:
%tensorboard --logdir=LSTM_logs

<div class="alert alert-block alert-warning">

__Key Observations:__
    
1. There is no improvement in our accuracy metrics as we are using Deep Learning Models.
    
2. They fail to converge at a point as we are using quite less amount of data and SGD with learning rate is not reaching a <code style="background:yellow;color:black">global minima.</code>

</div>